# Deteccion de aguaExample

Example on how to use the EBD Jupyterhub for Sentinel-1 time series processing



# 1. Import Modules

In [1]:
import os,sys

In [2]:
# Filesystem
#import fsspec
import s3fs

# EBD module
sys.path.append(os.path.join(os.environ['HOME'],'shared','teams','lib'))
import ebdpy as ebd
import importlib
importlib.reload(ebd)

<module 'ebdpy' from '/home/jovyan/shared/teams/lib/ebdpy.py'>

In [3]:
# Typical modules needed for computing and visuzlization (xarray and friends...)
import xarray as xr
import numpy as np
import pandas as pd
import hvplot.xarray
import cartopy
import panel as pn
import holoviews as hv
from holoviews import opts
%matplotlib inline
import matplotlib.pylab as plt
import matplotlib.patches as patches  # Needed to draw rectangles
import glob
from skimage import exposure # to enhance image display
import datetime as dt
import gdal

# * Custom modules
# **  Follow the example of adding the ebd module for custom .py python modules
# sys.path.append(os.path.join(os.environ['HOME'],'my,'path','to','directory','containing','module'))
# import mymodule as mm

# * Useful approach to update module in notebook
# * When we make changes to a custom module and want to have those loaded into the notebook, 
# * we can make use of the importlib module with the importlib.reload() function:

# import importlib
# importlib.reload(ebd)  # Example to reload the ebd module
# importlib.reload(mm)   # Add your client modules here

In [4]:
# TURN WARNINGS OFF
# import logging
# logging.getLogger("param.main").setLevel(logging.CRITICAL)
import warnings
warnings.filterwarnings("ignore")

In [5]:
# User defined functions
def time_label_from_idx(ds,idx):
    label=''
    for i in idx:
        t = ds.isel({'time':i})
        l =f'{t.time.values}'.split('T')[0]
        label += f'{l} '
    return label

### User Choices

The user can choose the use the first existing cluster found and determine the cluster options:

In [6]:
###################### USER CHOICES HERE #####################
par={
    # s3 Access:
    'use_shared_credentials':False, # Credentials to use for s3 access
    'profile':'ebdrow',
    'region':'us-east-1',
    'endpoint':'s3.wasabisys.com',  
    
    # Cluster:
    'shutdown':False,  # Automatically shutdown cluster after running the notebook?
    'use_existing_cluster':True,
    'c_idx':0, # index of found cluster to use (0=first cluster, best to leave as default)
    'c_environment':'seppo',
    'c_profile':'Medium Worker',
    # Set workers minimum and maximum desired in the cluster. 
    'worker_min':1,
    'worker_max':10,
    'adaptive_scaling':True,  # Chose whether to use adaptive (True) or fixed (False) scaling
    'wait_for_cluster':True  # True is important when the notebook is executed automatically or as script.
    }
##############################################################

In [7]:
par

{'use_shared_credentials': False,
 'profile': 'ebdrow',
 'region': 'us-east-1',
 'endpoint': 's3.wasabisys.com',
 'shutdown': False,
 'use_existing_cluster': True,
 'c_idx': 0,
 'c_environment': 'seppo',
 'c_profile': 'Medium Worker',
 'worker_min': 1,
 'worker_max': 10,
 'adaptive_scaling': True,
 'wait_for_cluster': True}

# 2. Establish a Cloud Filesystem

## Choose a config file with your s3 credentials 

Default to share is `$HOME/shared/.aws/credentials`

With the command below in a terminal, personal credentials can be set in a the personal config file `$HOME/.aws/credentials`:

```
    conda activate seppo  # for aws to work
    aws configure --profile ebdrow
```


In [8]:
use_shared_credentials=par['use_shared_credentials']

if use_shared_credentials:
    cfile=os.path.join(os.environ['HOME'],'shared','.aws','credentials')
else:
    cfile=os.path.join(os.environ['HOME'],'.aws','credentials')
print('s3 credentials from',cfile)

s3 credentials from /home/jovyan/.aws/credentials


We can list the profiles available in the cfile:

In [9]:
 ebd.list_profiles(cfile)

Your available profiles:
(/home/jovyan/.aws/credentials)
DEFAULT
w-ebd-public
ebdrow


In [10]:
# Set s3 parameters
profile =par['profile']
region  =par['region']
endpoint=par['endpoint']
# Choose your profile and endpoint
# profile='wasabi-europe'
# region='eu-central-1'
# endpoint=f's3.{region}.wasabisys.com'

In [11]:
cfile




'/home/jovyan/.aws/credentials'

... and set the environment variables with the credentials

In [12]:
#ebd.set_credentials(cfile=cfile,profile=profile,region=region,endpoint=endpoint)
ebd.set_credentials(profile=profile,region=region,endpoint=endpoint)


## Make a 'filesystem' from s3fs

Much simpler right now. No broadcast needed. Works well with get_mapper for zarr files.

In [13]:
endpoint_url='https://'+os.environ['AWS_S3_ENDPOINT']
profile=os.environ['AWS_DEFAULT_PROFILE']

In [14]:
print(endpoint_url,profile)

https://s3.wasabisys.com ebdrow


In [15]:
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url':endpoint_url}, key=os.environ['AWS_ACCESS_KEY_ID'], secret=os.environ['AWS_SECRET_ACCESS_KEY'])

# 3. Prepare Cluster

## Start the Dask Gateway, configure a Cluster and connect to a Client

Then we look at cluster options, to determine the desired `environment` and Cluster worker profile we want to use `gateway.cluster_options`

### Start the Gateway and see what Cluster Options we have

In [16]:
# Dask
from dask_gateway import Gateway
from dask.distributed import Client

In [17]:
gateway = Gateway()
gateway.cluster_options()

Box(children=(Box(children=(HTML(value='<h2>Cluster Options</h2>'), Box(children=(HTML(value="<p style='font-w…

In [18]:
if gateway.list_clusters():
    print('Existing Dask clusters:')
    j=0
    for c in gateway.list_clusters():
        print(f'Cluster Index c_idx: {j} / Name:',c.name,c.status)
        j+=1        
else:
    print('No Cluster running.')

No Cluster running.


Here we get information on running clusters:

### Start new cluster or connect to existing one

Depending on whether a cluster is running and we choose to use it, we connect to it or start a new one. We will see the GatewayCluster status as output.

In [19]:
# If no cluster is running, create a new one, else connect to the first one found (idx=0, change if other cluster should be running)
use_existing_cluster=par['use_existing_cluster']
if gateway.list_clusters() and use_existing_cluster:
    print('Using existing cluster.')
    cluster=gateway.connect(gateway.list_clusters()[par['c_idx']].name)  
else:
    print('Starting new cluster.')
    cluster = gateway.new_cluster(environment=par['c_environment'], profile=par['c_profile'])
cluster

Starting new cluster.


In the cell above numbers will change as workers become available or disappear, thus this is a good cell to monitor.

The cell below can be executed repeadedly after the cluster is running to adjust scaling (uncomment and adjust the lines for `worker_min` and `worker_max`:

In [20]:
worker_min=par['worker_min']
worker_max=par['worker_max']
adaptive_scaling=par['adaptive_scaling']
# Overwrite par file
#worker_min=5
# worker_max=10
# adaptive_scaling=True  # Chose whether to use adaptive (True) or fixed (False) scaling
if adaptive_scaling:
    print(f'Setting Adaptive Scaling min={worker_min}, max={worker_max}')
    cluster.adapt(minimum=worker_min, maximum=worker_max)
else:
    print(f'Setting Fixed Scaling workers={worker_max}')
    cluster.scale(worker_max)

Setting Adaptive Scaling min=1, max=10


### Connect Gateway Cluster to a Dask Client

In a last step to launch our kubernetes cluster, we connect the cluster to a dask Client and show the Dashboard link with

    client=Client(cluster)
   

In [21]:
client = Client(cluster)
client 

<Client: 'tls://10.10.1.125:37265' processes=0 threads=0, memory=0 B>

The Dashboard link can be opened in a new browser window, e.g. to keep on a separate monitor to watch the cluster in action. 
The link can alos be pasted into the Dask Extension URL field in the side bar which will enable the selection tabs for monitoring to show in JupyterLab. A successfull connection is shown by turning the gray tabs to orange.

## Waiting for the cluster to be running

If the `wait_for_cluster` variable was set to `True`, we use the `cluster.scheduler` to  check on status and wait until the minimum workers are up and running.

In [22]:
wait_for_cluster=par['wait_for_cluster']
from time import sleep
if wait_for_cluster:
    target_workers=par['worker_min'] if par['adaptive_scaling'] else par['worker_max']
    live_workers=len(list(cluster.scheduler_info['workers']))
    t=0
    interval=2
    print(f'Elapsed time to wait for {target_workers} live workers:\n{live_workers}/{target_workers} workers - {t} seconds',end='')
    while not live_workers>=target_workers:
        sleep(interval)
        t+=interval
        print(f'\r{live_workers}/{target_workers} workers - {t} seconds',end='')
        live_workers=len(list(cluster.scheduler_info['workers']))
    print(f'\r{live_workers}/{target_workers} workers - {t} seconds')

Elapsed time to wait for 1 live workers:
1/1 workers - 120 seconds


# 4. Work on a specific MGRS TILE

## Explore the filesystem 

We can explore the data sets we have available at this file system and our credentials

In [23]:
fs.ls('/')  # Lists all buckets

[]

In [24]:
zarrPrefix='sentinel-1-l22/zarr/mgrs'
mgrs_tiles = [x.split('/')[-1] for x in fs.ls(zarrPrefix)]  # Lists all MGRS tiles available in Zarr format

In [25]:
print('Available tiles in zarr format:\n',' '.join(mgrs_tiles))

Available tiles in zarr format:
 06WVS 14TPS 14TPT 14UPU 14UPV 15RTN 15RTP 15RUN 15RUP 15RVN 15RVP 15RWN 15RWP 15RXN 15RXP 15RYN 15RYP 15SWU 15SXR 15TTF 15TTG 15TVF 15TVG 15TWG 15TXG 15TYG 16PGA 16PGV 16PHA 16PHV 16RBT 16RBU 16RCT 16RCU 16RDU 16REU 16RFT 16RFU 16RGT 16RGU 17PMQ 17TPF 17TPG 18MVT 18MWT 18NUF 18NUG 18NUH 18NVF 18NVG 18NVH 18NVJ 18NWF 18NWG 18NWH 18NWJ 18NXF 18NXG 18PVR 18PVS 18PWR 18PWS 18STD 18STE 18SUD 18SUE 18SVD 18SVE 19LCF 19NBH 20NRH 20NRJ 21LWG 21LZF 21MXS 21NTC 21NTD 46REP 55HFA


In [26]:
tile='18PWR' #
nameres='20m' # Name of the resolution mode (20 meters)

In [27]:
zfiles=fs.ls('/'.join([zarrPrefix,tile,nameres]))
print('Idx ZarrFile')
for i in range(len(zfiles)):
    print(i,zfiles[i])

Idx ZarrFile
0 sentinel-1-l22/zarr/mgrs/18PWR/20m/18PWR_20m_A_077_vh_mtfil.zarr
1 sentinel-1-l22/zarr/mgrs/18PWR/20m/18PWR_20m_A_077_vv_mtfil.zarr
2 sentinel-1-l22/zarr/mgrs/18PWR/20m/18PWR_20m_A_150_vh_mtfil.zarr
3 sentinel-1-l22/zarr/mgrs/18PWR/20m/18PWR_20m_A_150_vv_mtfil.zarr
4 sentinel-1-l22/zarr/mgrs/18PWR/20m/18PWR_20m_D_069_vh_mtfil.zarr
5 sentinel-1-l22/zarr/mgrs/18PWR/20m/18PWR_20m_D_069_vv_mtfil.zarr
6 sentinel-1-l22/zarr/mgrs/18PWR/20m/18PWR_20m_D_142_vh_mtfil.zarr
7 sentinel-1-l22/zarr/mgrs/18PWR/20m/18PWR_20m_D_142_vv_mtfil.zarr


In [53]:
# Pick main zarr file for display via index
idx=7

## Open the files and Scale the SAR data to calibrated $\gamma^{0}$ backscatter

To convert between dB, amplitude, and power units in SAR data:

$\gamma^0[dB] = 10*log_{10}(\gamma^0[power])$

$\gamma^0[dB] = 10*log_{10}(\gamma^0[amplitude]^2)$


We store the data as linearly scaled amplitude (DN) in 16bit with a calibration factor of -83 dB according to

$\gamma^0[dB]=10*log_{10}(DN^2)-83$

Thus, in order to convert the data to power units (required for analysis when averaging or other mathmatical operations are involved) we need to apply the following formula:

$\gamma^0[power] = DN^2*CAL$ with $CAL=10^{-8.3}$


In [54]:
CAL=np.power(10,-8.3)
dslist=[]
for z in zfiles:
    fsz=fs.get_mapper(z)
    ds=xr.open_zarr(fsz,consolidated=True)
    # Convert scaled Amplitudes to linear power backscatter (and retaining the attributes)
    attrs=ds.attrs.copy()
    ds=(np.power(ds.astype(np.float32,keep_attrs=True),2)*CAL)
    ds = ds.where(ds>0) # Set data <= 0 to NaN
    ds.attrs=attrs
    dslist.append(ds)


In [55]:
ds=dslist[idx]
ds

<xarray.Dataset>
Dimensions:                       (time: 116, x: 5490, y: 5490)
Coordinates:
  * time                          (time) datetime64[ns] 2017-01-02 ... 2020-1...
  * x                             (x) float64 5e+05 5e+05 ... 6.098e+05
  * y                             (y) float64 1.1e+06 1.1e+06 ... 9.902e+05
Data variables:
    tile18PWR_20m_D_142_vv_mtfil  (time, y, x) float32 dask.array<chunksize=(20, 512, 512), meta=np.ndarray>
Attributes:
    crs:           +init=epsg:32618
    descriptions:  ['2017-01-02', '2017-01-26', '2017-02-19', '2017-03-03', '...
    is_tiled:      1
    nodatavals:    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0....
    offsets:       [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0....
    res:           [20.0, 20.0]
    scales:        [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1....
    transform:     [20.0, 0.0, 499980.0, 0.0, -20.0, 1100040.0]

In [56]:
name=list(ds.data_vars)[0]
try:
    epsg=int(ds.attrs['crs'].split(':')[1])
    southern_hemisphere=True if epsg > 32700 else False
    zone = epsg - 32700 if southern_hemisphere else epsg-32600
except:
    zone=int(name[4:6])
    southern_hemisphere=True if name[6] <= 'M' else False

crs=cartopy.crs.UTM(zone,southern_hemisphere=southern_hemisphere)
print(crs.proj4_params)

{'ellps': 'WGS84', 'proj': 'utm', 'units': 'm', 'zone': 18}


Holoview colors:
    
[http://holoviews.org/user_guide/Colormaps.html](http://holoviews.org/user_guide/Colormaps.html)
    
Holoviews tiles

[https://holoviews.org/reference/elements/bokeh/Tiles.html](https://holoviews.org/reference/elements/bokeh/Tiles.html)

In [57]:
# Selection widget
# clim=(0.0005,0.1) #vh
clim=(0.01,0.3)  # vv

# Temporary setting of time as string
tmptime=ds['time'].copy()
ds['time']=ds['time'].dt.strftime('%Y-%m-%d')
hvp  = ds.hvplot.image(x='x',y='y',cmap='gray',rasterize=True,clim=clim,
                       xlabel='Longitude',ylabel='Latitude',
                       frame_height=600,groupby='time',
                       widgets={'time':pn.widgets.Select},crs=crs,tiles='ESRI',
                      xformatter='%.0f',yformatter='%.0f',data_aspect=1,legend=True)
ds['time']=tmptime
del tmptime
hvp

Row
    [0] HoloViews(DynamicMap, widgets={'time': <class '...})
    [1] Column
        [0] WidgetBox
            [0] Select(margin=(20, 20, 20, 20), name='time', options=['2017-01-02', ...], value='2017-01-02', width=250)
        [1] VSpacer()

In [64]:
ds.time

<xarray.DataArray 'time' (time: 116)>
array(['2017-01-02T00:00:00.000000000', '2017-01-26T00:00:00.000000000',
       '2017-02-19T00:00:00.000000000', '2017-03-03T00:00:00.000000000',
       '2017-03-15T00:00:00.000000000', '2017-03-27T00:00:00.000000000',
       '2017-04-08T00:00:00.000000000', '2017-04-20T00:00:00.000000000',
       '2017-05-02T00:00:00.000000000', '2017-05-14T00:00:00.000000000',
       '2017-05-26T00:00:00.000000000', '2017-06-07T00:00:00.000000000',
       '2017-06-19T00:00:00.000000000', '2017-07-01T00:00:00.000000000',
       '2017-07-13T00:00:00.000000000', '2017-07-25T00:00:00.000000000',
       '2017-08-06T00:00:00.000000000', '2017-08-18T00:00:00.000000000',
       '2017-08-30T00:00:00.000000000', '2017-09-11T00:00:00.000000000',
       '2017-09-23T00:00:00.000000000', '2017-10-05T00:00:00.000000000',
       '2017-10-17T00:00:00.000000000', '2017-10-29T00:00:00.000000000',
       '2017-11-10T00:00:00.000000000', '2017-11-22T00:00:00.000000000',
       '2017-12-04T00:00:00.000000000', '2017-12-16T00:00:00.000000000',
       '2017-12-28T00:00:00.000000000', '2018-01-09T00:00:00.000000000',
       '2018-01-21T00:00:00.000000000', '2018-02-02T00:00:00.000000000',
       '2018-02-14T00:00:00.000000000', '2018-02-26T00:00:00.000000000',
       '2018-03-10T00:00:00.000000000', '2018-04-03T00:00:00.000000000',
       '2018-04-15T00:00:00.000000000', '2018-04-27T00:00:00.000000000',
       '2018-05-09T00:00:00.000000000', '2018-05-21T00:00:00.000000000',
       '2018-06-02T00:00:00.000000000', '2018-06-14T00:00:00.000000000',
       '2018-06-26T00:00:00.000000000', '2018-07-08T00:00:00.000000000',
       '2018-07-20T00:00:00.000000000', '2018-08-01T00:00:00.000000000',
       '2018-08-13T00:00:00.000000000', '2018-08-25T00:00:00.000000000',
       '2018-09-06T00:00:00.000000000', '2018-09-18T00:00:00.000000000',
       '2018-09-30T00:00:00.000000000', '2018-10-12T00:00:00.000000000',
       '2018-10-24T00:00:00.000000000', '2018-11-05T00:00:00.000000000',
       '2018-11-17T00:00:00.000000000', '2018-11-29T00:00:00.000000000',
       '2018-12-11T00:00:00.000000000', '2018-12-23T00:00:00.000000000',
       '2019-01-04T00:00:00.000000000', '2019-01-16T00:00:00.000000000',
       '2019-01-28T00:00:00.000000000', '2019-02-09T00:00:00.000000000',
       '2019-02-21T00:00:00.000000000', '2019-03-05T00:00:00.000000000',
       '2019-03-17T00:00:00.000000000', '2019-03-29T00:00:00.000000000',
       '2019-04-10T00:00:00.000000000', '2019-04-22T00:00:00.000000000',
       '2019-05-04T00:00:00.000000000', '2019-05-16T00:00:00.000000000',
       '2019-05-28T00:00:00.000000000', '2019-06-09T00:00:00.000000000',
       '2019-06-21T00:00:00.000000000', '2019-07-03T00:00:00.000000000',
       '2019-07-15T00:00:00.000000000', '2019-07-27T00:00:00.000000000',
       '2019-08-08T00:00:00.000000000', '2019-08-20T00:00:00.000000000',
       '2019-09-01T00:00:00.000000000', '2019-09-13T00:00:00.000000000',
       '2019-09-25T00:00:00.000000000', '2019-10-07T00:00:00.000000000',
       '2019-10-19T00:00:00.000000000', '2019-10-31T00:00:00.000000000',
       '2019-11-12T00:00:00.000000000', '2019-11-24T00:00:00.000000000',
       '2019-12-06T00:00:00.000000000', '2019-12-18T00:00:00.000000000',
       '2019-12-30T00:00:00.000000000', '2020-01-11T00:00:00.000000000',
       '2020-01-23T00:00:00.000000000', '2020-02-04T00:00:00.000000000',
       '2020-02-16T00:00:00.000000000', '2020-02-28T00:00:00.000000000',
       '2020-03-11T00:00:00.000000000', '2020-03-23T00:00:00.000000000',
       '2020-04-04T00:00:00.000000000', '2020-04-16T00:00:00.000000000',
       '2020-04-28T00:00:00.000000000', '2020-05-10T00:00:00.000000000',
       '2020-05-22T00:00:00.000000000', '2020-06-03T00:00:00.000000000',
       '2020-06-15T00:00:00.000000000', '2020-06-27T00:00:00.000000000',
       '2020-07-09T00:00:00.000000000', '2020-07-21T00:00:00.000000000',
       '2020-08-02T00:00:00.000000000', '2020-08-14T00:00:00.000000000',
       '2020-08-26T0

In [65]:
# Animation scrubber
clim=(0.0005,0.1)
clim=(0.01,0.3)  # vv

tmptime=ds['time'].copy()
ds['time']=ds['time'].dt.strftime('%Y-%m-%d')
hvp  = ds.isel(y=slice(0,2245)).hvplot.image(
    x='x',y='y',cmap='gray',rasterize=True,clim=clim,xlabel='Easting [m]',
    ylabel='Northing [m]',frame_width=800,groupby='time',
    widget_type='scrubber',widget_location='bottom',
    xformatter='%.0f',yformatter='%.0f',data_aspect=1)
ds['time']=tmptime
del tmptime
hvp

Column
    [0] HoloViews(DynamicMap, widget_location='bottom', widget_type='scrubber')
    [1] Row
        [0] HSpacer()
        [1] WidgetBox
            [0] Player(end=115, width=550)
        [2] HSpacer()

In [66]:
# Print the available dates in the time series
import datetime
for t in range(len(ds.time)):
    mytime=ds.isel(time=t).time.values
    date=str(mytime).split('T')[0]
    print(f'{t:3d} ',date,'   ',end='')
    if not (t+1)%5: print('')

  0  2017-01-02      1  2017-01-26      2  2017-02-19      3  2017-03-03      4  2017-03-15    
  5  2017-03-27      6  2017-04-08      7  2017-04-20      8  2017-05-02      9  2017-05-14    
 10  2017-05-26     11  2017-06-07     12  2017-06-19     13  2017-07-01     14  2017-07-13    
 15  2017-07-25     16  2017-08-06     17  2017-08-18     18  2017-08-30     19  2017-09-11    
 20  2017-09-23     21  2017-10-05     22  2017-10-17     23  2017-10-29     24  2017-11-10    
 25  2017-11-22     26  2017-12-04     27  2017-12-16     28  2017-12-28     29  2018-01-09    
 30  2018-01-21     31  2018-02-02     32  2018-02-14     33  2018-02-26     34  2018-03-10    
 35  2018-04-03     36  2018-04-15     37  2018-04-27     38  2018-05-09     39  2018-05-21    
 40  2018-06-02     41  2018-06-14     42  2018-06-26     43  2018-07-08     44  2018-07-20    
 45  2018-08-01     46  2018-08-13     47  2018-08-25     48  2018-09-06     49  2018-09-18    
 50  2018-09-30     51  2018-10-12     5

In [67]:
mid=int(ds.dims['time']/2)
idx=[0,mid,-1]
#idx=[108,108,107]
time1 = ds.isel({'time':idx[0]})
time2 = ds.isel({'time':idx[1]})
time3 = ds.isel({'time':idx[2]})

In [68]:
# time1  = ds.sel(time='2020-02-03T00:00:00.000000000')
# time2  = ds.sel(time='2020-02-15T00:00:00.000000000')

In [69]:
ts1=time1
ts2=time3

In [70]:
label1=f'{ts1.time.values}'.split('T')[0]
label2=f'{ts2.time.values}'.split('T')[0]

In [71]:

pre = ts1.load().hvplot.image(x='x',y='y',cmap='gray',rasterize=True,clim=clim,xlabel='Easting [m]',ylabel='Northing [m]',label=label1,frame_height=600,data_aspect=1)
post= ts2.load().hvplot.image(x='x',y='y',cmap='gray',rasterize=True,clim=clim,xlabel='Easting [m]',ylabel='Northing [m]',label=label2,frame_height=600,data_aspect=1)

In [72]:
(pre+post)

:Layout
   .DynamicMap.I  :DynamicMap   []
      :Image   [x,y]   (tile18PWR_20m_D_142_vv_mtfil)
   .DynamicMap.II :DynamicMap   []
      :Image   [x,y]   (tile18PWR_20m_D_142_vv_mtfil)

In [73]:
RGB=ds.isel({'time':idx})

In [74]:
RGB

<xarray.Dataset>
Dimensions:                       (time: 3, x: 5490, y: 5490)
Coordinates:
  * time                          (time) datetime64[ns] 2017-01-02 ... 2020-1...
  * x                             (x) float64 5e+05 5e+05 ... 6.098e+05
  * y                             (y) float64 1.1e+06 1.1e+06 ... 9.902e+05
Data variables:
    tile18PWR_20m_D_142_vv_mtfil  (time, y, x) float32 dask.array<chunksize=(1, 512, 512), meta=np.ndarray>
Attributes:
    crs:           +init=epsg:32618
    descriptions:  ['2017-01-02', '2017-01-26', '2017-02-19', '2017-03-03', '...
    is_tiled:      1
    nodatavals:    [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0....
    offsets:       [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0....
    res:           [20.0, 20.0]
    scales:        [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1....
    transform:     [20.0, 0.0, 499980.0, 0.0, -20.0, 1100040.0]

In [ ]:
rgb_stretched=ebd.rgb_stretch_ds(RGB)

In [ ]:
rgbplot=rgb_stretched.load().hvplot.rgb(rasterize=True,x='x',y='y',xlabel='Easting [m]',ylabel='Northing [m]',
                              label='RGB: '+time_label_from_idx(ds,idx),frame_height=800,frame_width=800,
                             xformatter='%.0f',yformatter='%.0f',data_aspect=1)
rgbplot

## Linking plots to show time series:

In [ ]:
pn.extension()

In [ ]:
clim=(0.0005,0.1)
clim=(0.01,0.3)  # vv

# image=ds.hvplot.image(x='x',y='y',cmap='gray',rasterize=True,clim=clim,
#                        xlabel='Easting [m]',ylabel='Northing [m]',
#                        frame_height=600,groupby='time',widgets={'time':pn.widgets.Select},crs=crs,tiles='ESRI',
#                       xformatter='%.0f',yformatter='%.0f',data_aspect=1,legend=True)
image=ds.isel(y=slice(0,2245)).hvplot.image(x='x',y='y',cmap='gray',rasterize=True,clim=clim,
                      xlabel='Easting [m]',ylabel='Northing [m]',
                      frame_width=600,groupby='time',fields={'time': {'default': ds.time.values[-1]}},
                      xformatter='%.0f',yformatter='%.0f',data_aspect=1,legend=True)

In [ ]:
stream=hv.streams.Tap(source=image,x=0,y=0)

In [ ]:
#stream.clear()

In [ ]:
list(ds.data_vars.variables.keys())[0]

In [ ]:
from numpy import log10
def timeseries(x,y):
    hvlist=[]
    title=f'x/y= {x:.0f} {y:.0f}'
    for ds in dslist:
        dB=10*log10(ds.sel(x=x,y=y,method='nearest'))
        name=' '.join(list(ds.data_vars.variables.keys())[0].split('_')[2:5])
        hvlist.append(dB.hvplot('time',ylim=[-40,-5],label=name,legend='left',ylabel='gamma_naught [dB]',xlabel='Date'))
    return hv.Overlay(hvlist).opts(show_legend=True,legend_position='right',title=title)

In [ ]:
pn.Column(image,pn.bind(timeseries, x=stream.param.x, y=stream.param.y))

# Flood Analysis Algorithm Tests

Let's try several approaches to flood mapping. We pick a flooding date t and compare the date to previous images

1) Gradient Threshold (GT):

If $abs(\gamma{^0}{_{t}} -  \gamma{^0}{_{t-1}}) > GT$, call it flooding

2) Standard Deviation Threshold (ST):
We pick a set of images predating the flooding date to compare against the image of the flood date:

- Images from a fixed period preceding t. e.g. 5 months
- Images from the same months in the preceding years
- Images from the same season in the preceding years

If $abs(\gamma{^0}{_{t}} -  \gamma{^0}{_{t-1}}) > ST$, call it flooding


## Select the Flood date image:


In [60]:
water=ds.median('time')
water_thres=0.024
water_mask=water<water_thres


In [61]:
#water_mask_ = water_mask.load().hvplot.image(x='x',y='y',cmap='Blues',rasterize=True,clim=clim,xlabel='Easting [m]',ylabel='Northing [m]',label=label1,frame_height=600,data_aspect=1)
#water_mask_
water_mask_ = water_mask.load().hvplot.image(x='x',y='y',cmap='Blues',rasterize=True,xlabel='Easting [m]',ylabel='Northing [m]',frame_height=600,data_aspect=1)
water_mask_
#water_mask.plot(cmap='Blues')

:DynamicMap   []
   :Image   [x,y]   (tile18PWR_20m_D_142_vv_mtfil)

In [62]:
dw=ds*water_mask
dw_mask=dw.mean('time')


In [63]:
water_mask__ = dw_mask.load().hvplot.image(x='x',y='y',cmap='Viridis',rasterize=True,xlabel='Easting [m]',ylabel='Northing [m]',frame_height=600,data_aspect=1)
water_mask__

:DynamicMap   []
   :Image   [x,y]   (tile18PWR_20m_D_142_vv_mtfil)

In [41]:
#dwmean=dw.mean('time')
#dwmin=dw.min('time')
#dwmax=dw.max('time')
#q=[0.02,.98]
#group = "U.S. Postage Rates (1999-2015)"
#dw_mean    = hv.Curve(dwmean, label='stamp', group=group)
#dw_min = hv.Curve(dwmin,  label='postcard', group=group)
#dw_max = hv.Curve(dwmax,  label='max', group=group)
#pulso = (dw_mean * dw_min * dw_max)
#dw_mean
#pulso.opts(opts.Curve(interpolation='steps-mid', width=400, height=400,line_dash=hv.Cycle(values=['dashed', 'solid'])),opts.Overlay(legend_position='top_left'))

## Save the classification image as a GeoTiff Bitmask

First, we are converting the classification result into a bitmask. NaN=0, other values=1

In [35]:
data_var=list(classified.data_vars)[0]
arr  = classified[data_var].values
arr[~np.isnan(arr)]=1
arr[np.isnan(arr)] =0
arr=arr.astype(np.uint8)
npixels=arr.sum()
print(f'{npixels} pixels found as classified')

1642222 pixels found as classified


Now we write the new array

In [38]:
outdir=os.path.join(os.environ['HOME'],'data','floodmasks')
os.makedirs(outdir, exist_ok=True)
filename=f'{data_var}_gradient_mask_{GT}.tif'
outname=os.path.join(outdir,filename)
projection=f'+proj=utm +zone={zone} +ellps=WGS84 +datum=WGS84 +units=m +no_defs'
geotrans=[float(ds.x[0].values)-10,20,0,float(ds.y[0].values)+10,0,-20]
print(f'Writing result to {outname}')

Writing result to /home/jovyan/data/floodmasks/tile15RWN_20m_A_063_vh_mtfil_gradient_mask_0.005.tif


Set a gdal `ColorTable` to apply to the output file

In [39]:
import gdal
# create color table
colors = gdal.ColorTable()
# set color blue for bitmask
colors.SetColorEntry(1, (0, 0, 244))

Write the file ...

In [40]:
_=ebd.CreateGeoTiff(outname,arr,bandnames=[f'Gradient Threshold {GT}'],GeoT=geotrans,Projection=projection,overwrite=True,colors=colors)

... and inspect it with `gdalinfo`

In [41]:
print(gdal.Info(outname))

Driver: GTiff/GeoTIFF
Files: /home/jovyan/data/floodmasks/tile15RWN_20m_A_063_vh_mtfil_gradient_mask_0.005.tif
Size is 5490, 5490
Coordinate System is:
PROJCRS["WGS 84 / UTM zone 15N",
    BASEGEOGCRS["WGS 84",
        DATUM["World Geodetic System 1984",
            ELLIPSOID["WGS 84",6378137,298.257223563,
                LENGTHUNIT["metre",1]]],
        PRIMEM["Greenwich",0,
            ANGLEUNIT["degree",0.0174532925199433]],
        ID["EPSG",4326]],
    CONVERSION["UTM zone 15N",
        METHOD["Transverse Mercator",
            ID["EPSG",9807]],
        PARAMETER["Latitude of natural origin",0,
            ANGLEUNIT["degree",0.0174532925199433],
            ID["EPSG",8801]],
        PARAMETER["Longitude of natural origin",-93,
            ANGLEUNIT["degree",0.0174532925199433],
            ID["EPSG",8802]],
        PARAMETER["Scale factor at natural origin",0.9996,
            SCALEUNIT["unity",1],
            ID["EPSG",8805]],
        PARAMETER["False easting",500000,
          

In [65]:
shutdown=par['shutdown']
# shutdown=True
if shutdown:
    cluster.shutdown()
    client.close()
    cluster=None
    client=None

In [66]:
shutdown

False

# Write the file to s3

In [10]:
use_shared_credentials=False

if use_shared_credentials:
    cfile=os.path.join(os.environ['HOME'],'shared','.aws','credentials')
else:
    cfile=os.path.join(os.environ['HOME'],'.aws','credentials')
print('s3 credentials from',cfile)

s3 credentials from /home/jovyan/.aws/credentials


We can list the profiles available in the cfile:

In [11]:
 ebd.list_profiles(cfile)

Your available profiles:
(/home/jovyan/.aws/credentials)
DEFAULT
wasabi_admin
wasabi


In [12]:
# Set s3 parameters
profile ='wasabi'
region  =par['region']
endpoint=par['endpoint']
# Choose your profile and endpoint
# profile='wasabi-europe'
# region='eu-central-1'
# endpoint=f's3.{region}.wasabisys.com'

... and set the environment variables with the credentials

In [13]:
ebd.set_credentials(cfile=cfile,profile=profile,region=region,endpoint=endpoint)

## Make a 'filesystem' from s3fs

Much simpler right now. No broadcast needed. Works well with get_mapper for zarr files.

In [14]:
endpoint_url='https://'+os.environ['AWS_S3_ENDPOINT']
profile=os.environ['AWS_DEFAULT_PROFILE']

In [15]:
print(endpoint_url,profile)

https://s3.wasabisys.com wasabi


In [16]:
fsw = s3fs.S3FileSystem(client_kwargs={'endpoint_url':endpoint_url}, key=os.environ['AWS_ACCESS_KEY_ID'], secret=os.environ['AWS_SECRET_ACCESS_KEY'])

In [17]:
fsw.ls('ebd-dev')

['ebd-dev/noaa']

In [50]:
?fsw.copy

Signature: fsw.copy(path1, path2, **kwargs)
Docstring: Copy within two locations in the filesystem
File:      /home/conda/store/802e4196e4af0f9dbc000362cdb3bfde2df34aa9512bcfa6511c384ccef4518f-seppo/lib/python3.7/site-packages/s3fs/core.py
Type:      method


In [51]:
pwd


'/home/jovyan/github/private/notebooks/qhub/shared/ebdall/notebooks/examples'

In [80]:
ls tile15RWN_20m_A_063_vh_mtfil_gradient_mask_0tile1055RWN_20m_A_063_vh_mtfil_gradient_mask_0.005.tif

ls: cannot access '/home/jovyan/data/floodmasks/tile1055RWN_20m_A_063_vh_mtfil_gradient_mask_0.005.tif': No such file or directory


In [81]:
ls /home/jovyan/data/floodmasks/tile15RWN_20m_A_063_vh_mtfil_gradient_mask_0.005.tif


/home/jovyan/data/floodmasks/tile15RWN_20m_A_063_vh_mtfil_gradient_mask_0.005.tif


In [82]:
outname

'/home/jovyan/data/floodmasks/tile15RWN_20m_A_063_vh_mtfil_gradient_mask_0.005.tif'

In [18]:
Bucket='ebd-dev'
Prefix='noaa-star/sar/floodmasks'

target='s3://'+'/'.join([Bucket,Prefix,os.path.basename(outname)])
print(f'Copy from {outname} to {target}')

NameError: name 'outname' is not defined

In [1]:
cmd=f'aws s3 cp --profile {profile} --endpoint-url {endpoint_url} {outname} {target}'
print(cmd)

NameError: name 'profile' is not defined

In [53]:
fsw.copy(outname,target)

PermissionError: Forbidden

In [90]:
fs.clear_instance_cache()